In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import display
import seaborn as sns

%matplotlib inline
plt.style.use('seaborn-notebook')
plt.rcParams["figure.figsize"] = (20, 3)
pd.options.display.float_format = '{:20,.4f}'.format
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
sns.set(context="paper", font="monospace")

from sklearn.preprocessing import LabelEncoder,StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, r2_score, mean_squared_error
from sklearn.linear_model import LinearRegression, LogisticRegression
import warnings
warnings.filterwarnings('ignore')

from sklearn.metrics import log_loss, roc_auc_score

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier,AdaBoostRegressor
from sklearn.tree import DecisionTreeClassifier

In [3]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')
sub = pd.read_csv('SampleSubmission.csv')

In [4]:
train.drop(['form_field40', 'form_field31','form_field41','form_field11', 'form_field45'],axis=1, inplace = True)
test.drop(['form_field40', 'form_field31','form_field41','form_field11', 'form_field45'],axis=1, inplace = True)            

In [5]:
test['default_status'] = 'test'
data = pd.concat([train, test]).reset_index(drop=True)

In [6]:
missing_col = data.columns[data.isna().any()]
missing_col

Index(['form_field1', 'form_field2', 'form_field3', 'form_field4',
       'form_field5', 'form_field6', 'form_field7', 'form_field8',
       'form_field9', 'form_field10', 'form_field12', 'form_field13',
       'form_field15', 'form_field16', 'form_field17', 'form_field18',
       'form_field19', 'form_field20', 'form_field21', 'form_field22',
       'form_field23', 'form_field24', 'form_field25', 'form_field26',
       'form_field27', 'form_field28', 'form_field29', 'form_field30',
       'form_field32', 'form_field33', 'form_field34', 'form_field35',
       'form_field36', 'form_field37', 'form_field38', 'form_field39',
       'form_field42', 'form_field43', 'form_field44', 'form_field46',
       'form_field48', 'form_field49', 'form_field50'],
      dtype='object')

In [7]:
for col in missing_col:
    
    data[col].fillna(data[col].median(), inplace = True)

In [8]:
data.isnull().sum()

Applicant_ID      0
form_field1       0
form_field2       0
form_field3       0
form_field4       0
form_field5       0
form_field6       0
form_field7       0
form_field8       0
form_field9       0
form_field10      0
form_field12      0
form_field13      0
form_field14      0
form_field15      0
form_field16      0
form_field17      0
form_field18      0
form_field19      0
form_field20      0
form_field21      0
form_field22      0
form_field23      0
form_field24      0
form_field25      0
form_field26      0
form_field27      0
form_field28      0
form_field29      0
form_field30      0
form_field32      0
form_field33      0
form_field34      0
form_field35      0
form_field36      0
form_field37      0
form_field38      0
form_field39      0
form_field42      0
form_field43      0
form_field44      0
form_field46      0
form_field47      0
form_field48      0
form_field49      0
form_field50      0
default_status    0
dtype: int64

In [9]:
data.describe(include='all')

Applicant_ID          form_field1          form_field2  \
count           80000          80,000.0000          80,000.0000   
unique          80000                  nan                  nan   
top     Apcnt_1123552                  nan                  nan   
freq                1                  nan                  nan   
mean              NaN           3,491.5809               0.5331   
std               NaN             184.7323               0.7968   
min               NaN           2,986.0000               0.0000   
25%               NaN           3,366.0000               0.0800   
50%               NaN           3,484.0000               0.2695   
75%               NaN           3,612.0000               0.6792   
max               NaN           3,900.0000              22.3150   

                form_field3          form_field4          form_field5  \
count           80,000.0000          80,000.0000          80,000.0000   
unique                  nan                  nan                  nan   
top                     nan                  nan                  nan   
freq                    nan                  nan                  nan   
mean                 1.0500               0.8488               2.0118   
std                  2.1577               3.2238              10.7592   
min                  0.0000               0.0000               0.0000   
25%                  0.0000               0.0000               0.0000   
50%                  0.0600               0.0000               0.0000   
75%                  1.2746               0.0000               0.0000   
max                 57.3716             206.4528             407.7486   

                form_field6          form_field7          form_field8  \
count           80,000.0000          80,000.0000          80,000.0000   
unique                  nan                  nan                  nan   
top                     nan                  nan                  nan   
freq                    nan                  nan                  nan   
mean           504,236.3583       6,462,628.1600       2,238,848.3195   
std          1,276,940.5801      17,488,905.8669       3,513,809.2259   
min                  0.0000               0.0000               0.0000   
25%             35,010.0000         811,843.0000         319,758.0000   
50%            115,533.0000       2,710,163.0000         963,942.0000   
75%            306,532.0000       6,354,023.2500       2,402,075.0000   
max         53,135,455.0000   2,158,794,400.0000     113,514,090.0000   

                form_field9         form_field10         form_field12  \
count           80,000.0000          80,000.0000          80,000.0000   
unique                  nan                  nan                  nan   
top                     nan                  nan                  nan   
freq                    nan                  nan                  nan   
mean        12,158,555.3064      11,810,270.7110       2,487,520.2115   
std         19,416,348.2550      26,058,050.8968       4,239,615.6898   
min                  0.0000               0.0000               0.0000   
25%          1,831,023.0000         452,407.0000         404,949.0000   
50%          5,512,519.0000       3,692,582.5000       1,158,247.5000   
75%         14,121,283.5000      13,135,849.2500       2,684,878.0000   
max      1,443,921,320.0000   2,191,361,480.0000     160,923,465.0000   

               form_field13         form_field14         form_field15  \
count           80,000.0000          80,000.0000          80,000.0000   
unique                  nan                  nan                  nan   
top                     nan                  nan                  nan   
freq                    nan                  nan                  nan   
mean         5,541,622.9248      76,279,711.7706     102,246,169.9499   
std         21,112,009.0022   3,068,578,796.1942      91,473,037.3532   
min                  0.0000               0.0000         539,5

In [10]:
from scipy.stats import skew,norm  # for some statistics

In [11]:
numeric = data.select_dtypes(include='number').columns
skew_features = data[numeric].apply(lambda x: skew(x)).sort_values(ascending=True)

high_skew = skew_features[skew_features > 0.5]
skew_index = high_skew.index

print("There are {} numerical features with Skew > 0.5 :".format(high_skew.shape[0]))
skewness = pd.DataFrame({'Skew' :high_skew})
skew_features

There are 41 numerical features with Skew > 0.5 :


form_field44                -0.5029
form_field30                -0.1981
form_field1                  0.1248
form_field29                 0.9388
form_field28                 0.9911
form_field22                 1.1656
form_field42                 1.2129
form_field21                 1.5684
form_field33                 1.5974
form_field26                 1.6516
form_field43                 1.6586
form_field27                 1.6741
form_field25                 1.8046
form_field37                 2.1489
form_field23                 2.5311
form_field32                 2.5638
form_field49                 2.5952
form_field36                 2.6840
form_field38                 2.7596
form_field20                 3.1420
form_field19                 3.2760
form_field3                  4.2203
form_field2                  4.5311
form_field16                 4.5474
form_field8                  4.5749
form_field18                 5.1708
form_field17                 5.2843
form_field35                

In [12]:
# Normalize skewed features using log transformation
for column in skew_index:
    data[column] = np.log1p(data[column])

In [13]:
cat_features = data.select_dtypes(exclude=np.number).columns.drop('default_status')

In [14]:
cat_features

Index(['Applicant_ID', 'form_field47'], dtype='object')

In [15]:
data.drop('Applicant_ID',inplace=True,axis=1)

In [16]:
dissected = pd.get_dummies(data[['form_field47']])

In [17]:
data = data.join(dissected)

In [18]:
data.drop(['form_field47'], inplace=True, axis=1)

In [19]:
data.head(2)

form_field1          form_field2          form_field3  \
0           3,436.0000               0.2508               0.9768   
1           3,456.0000               0.5152               0.2104   

           form_field4          form_field5          form_field6  \
0               0.0000               0.0000               0.0000   
1               0.0000               0.0000               0.0000   

           form_field7          form_field8          form_field9  \
0              16.1848              12.4375              15.2678   
1              13.7090              13.1174              16.0209   

          form_field10         form_field12         form_field13  \
0              16.2432              14.6490              15.8793   
1              14.7450              15.1975              14.5770   

          form_field14         form_field15         form_field16  \
0              18.3838              18.5356               0.6931   
1              17.1528              17.6259               0.6931   

          form_field17         form_field18         form_field19  \
0               0.6931               0.6931               1.3863   
1               0.6931               0.6931               1.0986   

          form_field20         form_field21         form_field22  \
0               1.3863               4.9101               8.6933   
1               1.0986               4.7026               9.3402   

          form_field23         form_field24         form_field25  \
0               8.6217               4.9101               8.2944   
1               9.5878               4.4738               8.3338   

          form_field26         form_field27         form_field28  \
0               9.7448               9.3393               4.1109   
1               9.5041               9.0986               5.7203   

          form_field29         form_field30         form_field32  \
0               9.7448           5,962.0000               6.9594   
1               9.5041           5,780.0000               7.8458   

          form_field33         form_field34         form_field35  \
0               2.1972               1.0986               0.0000   
1               2.9178               0.0000               0.0000   

          form_field36         form_field37         form_field38  \
0               2.5649               2.5649               1.6094   
1               2.8332               3.2189               2.1972   

          form_field39         form_field42         form_field43  \
0               0.0000               0.3314               1.1053   
1               0.0000               0.2733               2.2061   

          form_field44         form_field46         form_field48  \
0               0.7116               0.0000               5.7611   
1               0.1836               0.0000               5.8602   

          form_field49         form_field50 default_status  \
0               0.7559               0.0434             no   
1               0.9634               0.2795             no   

   form_field47_charge  form_field47_lending  
0                    1                     0  
1                    1                     0

In [20]:
train_df = data.loc[( data['default_status'] != 'test')].reset_index(drop = True)
test_df = data.loc[( data['default_status'] == 'test')].reset_index(drop = True)

In [21]:
train_df.shape, test_df.shape

((56000, 47), (24000, 47))

In [22]:
X = train_df.drop('default_status', axis = 1)
y = train_df['default_status']

In [23]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3,stratify = y,  random_state=42)

In [24]:
lr = LogisticRegression()
rf = RandomForestClassifier()
gbm = GradientBoostingClassifier()
decision_tree = DecisionTreeClassifier()

In [25]:
lr.fit(X_train, y_train)
rf.fit(X_train, y_train)
gbm.fit(X_train, y_train)
decision_tree.fit(X_train, y_train)

DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='gini',
                       max_depth=None, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=None, splitter='best')

In [26]:
print('Logistic Regression Log loss: {}'.format(roc_auc_score(y_test, lr.predict_proba(X_test)[:,1])))
print('RandomForestClassifier Log loss: {}'.format(roc_auc_score(y_test, rf.predict_proba(X_test)[:,1])))
print('GradientBoostingClassifier Log loss: {}'.format(roc_auc_score(y_test, gbm.predict_proba(X_test)[:,1])))
print('DecisionTreeClassifier Log loss: {}'.format(roc_auc_score(y_test, decision_tree.predict_proba(X_test)[:,1])))

Logistic Regression Log loss: 0.802175117000884
RandomForestClassifier Log loss: 0.8276666536884967
GradientBoostingClassifier Log loss: 0.8351402017895926
DecisionTreeClassifier Log loss: 0.6416058461852343


In [27]:
accuracy = gbm.score(X_test, y_test)

In [28]:
accuracy

0.8110119047619048

In [29]:
test_x = test_df.drop('default_status', axis = 1)

In [30]:
prediction = gbm.predict(test_x)

In [31]:
sub['default_status'] = prediction
sub.to_csv('MySubmission.csv', index =False)

In [32]:
sub

Applicant_ID default_status
0      Apcnt_1000032             no
1      Apcnt_1000048             no
2      Apcnt_1000052             no
3      Apcnt_1000076            yes
4      Apcnt_1000080             no
5      Apcnt_1000084             no
6      Apcnt_1000104             no
7      Apcnt_1000116            yes
8      Apcnt_1000128             no
9      Apcnt_1000156             no
10     Apcnt_1000192             no
11     Apcnt_1000208             no
12     Apcnt_1000264            yes
13     Apcnt_1000288             no
14     Apcnt_1000292            yes
15     Apcnt_1000328            yes
16     Apcnt_1000336             no
17     Apcnt_1000356             no
18     Apcnt_1000368             no
19     Apcnt_1000372            yes
20     Apcnt_1000392             no
21     Apcnt_1000396             no
22     Apcnt_1000400             no
23     Apcnt_1000416             no
24     Apcnt_1000428             no
25     Apcnt_1000440             no
26     Apcnt_1000456            yes
27     Apcnt_1000472             no
28     Apcnt_1000488             no
29     Apcnt_1000492             no
30     Apcnt_1000504            yes
31     Apcnt_1000516             no
32     Apcnt_1000532             no
33     Apcnt_1000552             no
34     Apcnt_1000564             no
35     Apcnt_1000576            yes
36     Apcnt_1000596             no
37     Apcnt_1000620             no
38     Apcnt_1000624             no
39     Apcnt_1000636             no
40     Apcnt_1000648             no
41     Apcnt_1000668             no
42     Apcnt_1000680             no
43     Apcnt_1000696             no
44     Apcnt_1000704            yes
45     Apcnt_1000724             no
46     Apcnt_1000740             no
47     Apcnt_1000744             no
48     Apcnt_1000756             no
49     Apcnt_1000768             no
50     Apcnt_1000784             no
51     Apcnt_1000796             no
52     Apcnt_1000808             no
53     Apcnt_1000816             no
54     Apcnt_1000820             no
55     Apcnt_1000824             no
56     Apcnt_1000856            yes
57     Apcnt_1000872            yes
58     Apcnt_1000880             no
59     Apcnt_1000904             no
60     Apcnt_1000912            yes
61     Apcnt_1000920            yes
62     Apcnt_1000952             no
63     Apcnt_1000960             no
64     Apcnt_1000964             no
65     Apcnt_1000968             no
66     Apcnt_1000976            yes
67     Apcnt_1000984            yes
68     Apcnt_1000992             no
69     Apcnt_1000996            yes
70     Apcnt_1001000             no
71     Apcnt_1001008             no
72     Apcnt_1001028             no
73     Apcnt_1001032            yes
74     Apcnt_1001036            yes
75     Apcnt_1001040            yes
76     Apcnt_1001048            yes
77     Apcnt_1001052             no
78     Apcnt_1001068            yes
79     Apcnt_1001076             no
80     Apcnt_1001080             no
81     Apcnt_1001092             no
82     Apcnt_1001120            yes
83     Apcnt_1001144            yes
84     Apcnt_1001148             no
85     Apcnt_1001168             no
86     Apcnt_1001176            yes
87     Apcnt_1001200             no
88     Apcnt_1001224             no
89     Apcnt_1001228             no
90     Apcnt_1001236             no
91     Apcnt_1001244             no
92     Apcnt_1001248             no
93     Apcnt_1001256             no
94     Apcnt_1001260             no
95     Apcnt_1001264             no
96     Apcnt_1001288             no
97     Apcnt_1001292             no
98     Apcnt_1001296             no
99     Apcnt_1001304             no
100    Apcnt_1001308             no
101    Apcnt_1001316             no
102    Apcnt_1001320             no
103    Apcnt_1001352             no
104    Apcnt_1001360             no
105    Apcnt_1001376            yes
106    Apcnt_1001384             no
107    Apcnt_1001388             no
108    Apcnt_1001400            yes
109    Apcnt_1001416            yes
110    Apcnt